# Artificial Neural Network to predict which clients will leave the bank

Use an Artificial Neural Network (ANN) to predict if a specific clients will leave the bank or not, using the clients informations including the credit score, geography, gender ...

In the last part of this notebook we will tune the hyperparameter of our model using a GridSearch crossvalidation

## Part 1 - Data Preprocessing

In [1]:
# Importing the libraries
import multiprocessing
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from sklearn.preprocessing import LabelEncoder, OneHotEncoder
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import GridSearchCV
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import confusion_matrix
import keras
from keras.models import Sequential
from keras.layers import Dense, Dropout
from keras.wrappers.scikit_learn import KerasClassifier

Using TensorFlow backend.


In [31]:
# Importing the data set
dataset = pd.read_csv('Churn_Modelling.csv')
dataset.head()

RowNumber  CustomerId   Surname  CreditScore Geography  Gender  Age  \
0          1    15634602  Hargrave          619    France  Female   42   
1          2    15647311      Hill          608     Spain  Female   41   
2          3    15619304      Onio          502    France  Female   42   
3          4    15701354      Boni          699    France  Female   39   
4          5    15737888  Mitchell          850     Spain  Female   43   

   Tenure    Balance  NumOfProducts  HasCrCard  IsActiveMember  \
0       2       0.00              1          1               1   
1       1   83807.86              1          0               1   
2       8  159660.80              3          1               0   
3       1       0.00              2          0               0   
4       2  125510.82              1          1               1   

   EstimatedSalary  Exited  
0        101348.88       1  
1        112542.58       0  
2        113931.57       1  
3         93826.63       0  
4         79084.10       0

We will not include all the variables in our model. In particular some of them are irrelevant like CustomerId andSurname. Exited column will represent our target y

In [3]:
X = dataset.iloc[:, 3:13]
y = dataset.iloc[:, 13]

Since we have some categorical data in our dataset (Geography, Gender) we will have to encode them into numerical values

In [4]:
# Encode the categorical data
encoder_X_1 = LabelEncoder()
X.iloc[:, 1] = encoder_X_1.fit_transform(X.iloc[:, 1])
# We need two encoder since we have two categorical variable
encoder_X_2 = LabelEncoder()
X.iloc[:, 2] = encoder_X_2.fit_transform(X.iloc[:, 2])
X.head()

CreditScore  Geography  Gender  Age  Tenure    Balance  NumOfProducts  \
0          619          0       0   42       2       0.00              1   
1          608          2       0   41       1   83807.86              1   
2          502          0       0   42       8  159660.80              3   
3          699          0       0   39       1       0.00              2   
4          850          2       0   43       2  125510.82              1   

   HasCrCard  IsActiveMember  EstimatedSalary  
0          1               1        101348.88  
1          0               1        112542.58  
2          1               0        113931.57  
3          0               0         93826.63  
4          1               1         79084.10

In [5]:
# use pd.concat to join the new columns with the original dataframe
X = pd.concat([X,pd.get_dummies(X['Geography'], prefix='Geography',drop_first=True)],axis=1)
X.drop(['Geography'],axis=1, inplace=True)
X.head()

CreditScore  Gender  Age  Tenure    Balance  NumOfProducts  HasCrCard  \
0          619       0   42       2       0.00              1          1   
1          608       0   41       1   83807.86              1          0   
2          502       0   42       8  159660.80              3          1   
3          699       0   39       1       0.00              2          0   
4          850       0   43       2  125510.82              1          1   

   IsActiveMember  EstimatedSalary  Geography_1  Geography_2  
0               1        101348.88            0            0  
1               1        112542.58            0            1  
2               0        113931.57            0            0  
3               0         93826.63            0            0  
4               1         79084.10            0            1

Now we will split the dataset into Training and Test set

In [6]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, random_state = 0)
print('X Train: ' + str(X_train.shape))
print('y Train: ' + str(y_train.shape))
print('X Test: ' + str(X_test.shape))
print('y Test: ' + str(y_test.shape))

X Train: (8000, 11)
y Train: (8000,)
X Test: (2000, 11)
y Test: (2000,)


In general features scaling is necessary in Artificial Neural Networks because there are lot of computantions and highly computive power calculation. Feautures scaling helps to ease them

In [7]:
# Feature Scaling
sc = StandardScaler()
X_train = sc.fit_transform(X_train)
X_test = sc.transform(X_test)

## Part 2 - Build the ANN

Since there is no rule to choose the number of layers and neurons for our neural networks, we will try different combinations of them. For the number of neurons we can try to use a common rule that indicates the number of hidden neurons as the average between the number of nodes in the input and in the output

In [15]:
# Build the model
mdl = Sequential()
# First hidden layer
mdl.add(Dense(6, kernel_initializer = 'uniform', activation = 'relu', input_dim = X_train.shape[1]))
# Second hidden layer
mdl.add(Dense(6, kernel_initializer = 'uniform', activation = 'relu'))
# Output layer
mdl.add(Dense(1, kernel_initializer = 'uniform', activation = 'sigmoid' ))

Using the sigmoid activation function in the output layer, the model will output probabilities.

In [16]:
# Compile the model
mdl.compile(optimizer = 'adam', loss = 'binary_crossentropy', metrics = ['accuracy'])

In [17]:
# Fitting the ANN to the Training Set
mdl.fit(x = X_train, y = y_train, batch_size = 10, epochs = 100)

Epoch 1/100
8000/8000 [==============================] - 1s 180us/step - loss: 0.4777 - acc: 0.7960
Epoch 2/100
8000/8000 [==============================] - 1s 135us/step - loss: 0.4254 - acc: 0.7960
Epoch 3/100
8000/8000 [==============================] - 1s 160us/step - loss: 0.4188 - acc: 0.8140
Epoch 4/100
8000/8000 [==============================] - 1s 153us/step - loss: 0.4167 - acc: 0.8269
Epoch 5/100
8000/8000 [==============================] - 1s 134us/step - loss: 0.4144 - acc: 0.8314
Epoch 6/100
8000/8000 [==============================] - 1s 134us/step - loss: 0.4127 - acc: 0.8324
Epoch 7/100
8000/8000 [==============================] - 1s 130us/step - loss: 0.4116 - acc: 0.8307
Epoch 8/100
8000/8000 [==============================] - 1s 136us/step - loss: 0.4102 - acc: 0.8326
Epoch 9/100
8000/8000 [==============================] - 1s 133us/step - loss: 0.4091 - acc: 0.8347
Epoch 10/100
8000/8000 [==============================] - 1s 134us/step - loss: 0.4080 - acc: 0.8341

## Part 3 - Making the predictions

In [19]:
# Predict test set results
y_pred = mdl.predict(X_test)

As we said before, in this case the output will be a probability. For this reason, to have a binary output, we need to choose a threshold to convert the probabilities. In this case we will use a threshold of 0.5

In [20]:
y_pred = (y_pred > 0.5)
y_pred

array([[False],
       [False],
       [False],
       ..., 
       [False],
       [False],
       [False]], dtype=bool)

In [21]:
# Confusion Matrix Calculation
conf_matrix = confusion_matrix(y_test, y_pred)
TP = conf_matrix[0][0]
FN = conf_matrix[0][1]
TN = conf_matrix[1][1]
FP = conf_matrix[1][0]

In [22]:
print('True Positive: ' + str(TP))
print('False Positive: ' + str(FP))
print('True Negative: ' + str(TN))
print('False Negative: ' + str(FN))

True Positive: 1536
False Positive: 59
True Negative: 149
False Negative: 256


In [25]:
# Accuracy on test set
acc = (TP + TN) / (TP + FP + FN + TN)
print( ' Accuracy on Test set :' + str(acc))

 Accuracy on Test set :0.8425


## Part 4 - Evaluate, Improving, Tuning the ANN

To evaluate the ANN we will use 10-fold crossvalidation. We also add Dropout regularization to avoid overfitting

In [56]:
# Function that builds the ANN in the same way as before
def build_classifier(optimizer):
    mdl = Sequential()
    mdl.add(Dense(60, kernel_initializer = 'uniform', activation = 'relu', input_dim = X_train.shape[1]))
    mdl.add(Dropout(0.2))
    mdl.add(Dense(30, kernel_initializer = 'uniform', activation = 'relu', input_dim = X_train.shape[1]))
    mdl.add(Dropout(0.2))
    mdl.add(Dense(1, kernel_initializer = 'uniform', activation = 'sigmoid' ))
    mdl.compile(optimizer = optimizer, loss = 'binary_crossentropy', metrics = ['accuracy'])
    return mdl

In [55]:
def build_classifier2():
    mdl = Sequential()
    mdl.add(Dense(60, kernel_initializer = 'uniform', activation = 'relu', input_dim = X_train.shape[1]))
    mdl.add(Dropout(0.2))
    mdl.add(Dense(30, kernel_initializer = 'uniform', activation = 'relu', input_dim = X_train.shape[1]))
    mdl.add(Dropout(0.2))
    mdl.add(Dense(1, kernel_initializer = 'uniform', activation = 'sigmoid' ))
    mdl.compile(optimizer = 'adam', loss = 'binary_crossentropy', metrics = ['accuracy'])
    return mdl

Now we will train the classifier on 9 folds and test on 1 fold, for each of the 10 folds

In [58]:
classifier = KerasClassifier(build_fn = build_classifier2, batch_size = 10000, epochs = 1000)

In [64]:
# All the accuracy scores returned by 10 fold crossvalidation
accuracies = cross_val_score(estimator = classifier, X = X_train, y = y_train, cv = 10, n_jobs = 1)

Epoch 1/1000
7200/7200 [==============================] - 9s 1ms/step - loss: 0.6928 - acc: 0.6637
Epoch 2/1000
7200/7200 [==============================] - 0s 5us/step - loss: 0.6921 - acc: 0.7953
Epoch 3/1000
7200/7200 [==============================] - 0s 5us/step - loss: 0.6914 - acc: 0.7971
Epoch 4/1000
7200/7200 [==============================] - 0s 5us/step - loss: 0.6905 - acc: 0.7971
Epoch 5/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.6897 - acc: 0.7971
Epoch 6/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.6888 - acc: 0.7971
Epoch 7/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.6878 - acc: 0.7971
Epoch 8/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.6868 - acc: 0.7971
Epoch 9/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.6857 - acc: 0.7971
Epoch 10/1000
7200/7200 [==============================] - 0s 5us/step - loss: 0.6845 - acc: 0.7971
Epoch 11/

7200/7200 [==============================] - 0s 4us/step - loss: 0.4438 - acc: 0.7971
Epoch 84/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4429 - acc: 0.7971
Epoch 85/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4428 - acc: 0.7971
Epoch 86/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.4412 - acc: 0.7971
Epoch 87/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4422 - acc: 0.7971
Epoch 88/1000
7200/7200 [==============================] - 0s 5us/step - loss: 0.4415 - acc: 0.7971
Epoch 89/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4410 - acc: 0.7971
Epoch 90/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4402 - acc: 0.7971
Epoch 91/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4387 - acc: 0.7971
Epoch 92/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4379 - acc: 0.7971
Epoch 93/1000


Epoch 165/1000
7200/7200 [==============================] - 0s 5us/step - loss: 0.4223 - acc: 0.8099
Epoch 166/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4239 - acc: 0.8071
Epoch 167/1000
7200/7200 [==============================] - 0s 5us/step - loss: 0.4227 - acc: 0.8110
Epoch 168/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4248 - acc: 0.8090
Epoch 169/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4235 - acc: 0.8108
Epoch 170/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4233 - acc: 0.8121
Epoch 171/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4241 - acc: 0.8124
Epoch 172/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4250 - acc: 0.8110
Epoch 173/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4226 - acc: 0.8117
Epoch 174/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4226 - ac

7200/7200 [==============================] - 0s 4us/step - loss: 0.4114 - acc: 0.8193
Epoch 247/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4117 - acc: 0.8221
Epoch 248/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4142 - acc: 0.8208
Epoch 249/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4110 - acc: 0.8244
Epoch 250/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4119 - acc: 0.8219
Epoch 251/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4095 - acc: 0.8213
Epoch 252/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4100 - acc: 0.8224
Epoch 253/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4112 - acc: 0.8240
Epoch 254/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4100 - acc: 0.8226
Epoch 255/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.4109 - acc: 0.8225
Epoch

Epoch 328/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3962 - acc: 0.8358
Epoch 329/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3986 - acc: 0.8356
Epoch 330/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3971 - acc: 0.8360
Epoch 331/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3993 - acc: 0.8378
Epoch 332/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3976 - acc: 0.8361
Epoch 333/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3980 - acc: 0.8363
Epoch 334/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4000 - acc: 0.8342
Epoch 335/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3985 - acc: 0.8361
Epoch 336/1000
7200/7200 [==============================] - 0s 5us/step - loss: 0.3956 - acc: 0.8371
Epoch 337/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3947 - ac

...

Epoch 633/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3801 - acc: 0.8443
Epoch 634/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3759 - acc: 0.8431
Epoch 635/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3770 - acc: 0.8443
Epoch 636/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3781 - acc: 0.8457
Epoch 637/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3784 - acc: 0.8439
Epoch 638/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3738 - acc: 0.8468
Epoch 639/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3740 - acc: 0.8446
Epoch 640/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3763 - acc: 0.8453
Epoch 641/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3769 - acc: 0.8472
Epoch 642/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3819 - ac

7200/7200 [==============================] - 0s 4us/step - loss: 0.3736 - acc: 0.8456
Epoch 715/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3725 - acc: 0.8453
Epoch 716/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3685 - acc: 0.8499
Epoch 717/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3702 - acc: 0.8497
Epoch 718/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3670 - acc: 0.8489
Epoch 719/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3691 - acc: 0.8467
Epoch 720/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3713 - acc: 0.8457
Epoch 721/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3654 - acc: 0.8500
Epoch 722/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3681 - acc: 0.8503
Epoch 723/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3667 - acc: 0.8497
Epoch

Epoch 796/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3547 - acc: 0.8532
Epoch 797/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3542 - acc: 0.8550
Epoch 798/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3504 - acc: 0.8521
Epoch 799/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3534 - acc: 0.8551
Epoch 800/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3513 - acc: 0.8565
Epoch 801/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3529 - acc: 0.8550
Epoch 802/1000
7200/7200 [==============================] - 0s 5us/step - loss: 0.3586 - acc: 0.8525
Epoch 803/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3536 - acc: 0.8553
Epoch 804/1000
7200/7200 [==============================] - 0s 5us/step - loss: 0.3519 - acc: 0.8537
Epoch 805/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3561 - ac

Epoch 878/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3458 - acc: 0.8606
Epoch 879/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3403 - acc: 0.8587
Epoch 880/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3427 - acc: 0.8632
Epoch 881/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3443 - acc: 0.8572
Epoch 882/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3489 - acc: 0.8599
Epoch 883/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3424 - acc: 0.8587
Epoch 884/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3387 - acc: 0.8615
Epoch 885/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3442 - acc: 0.8594
Epoch 886/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3483 - acc: 0.8560
Epoch 887/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3421 - ac

7200/7200 [==============================] - 0s 6us/step - loss: 0.3406 - acc: 0.8612
Epoch 960/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3401 - acc: 0.8628
Epoch 961/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3402 - acc: 0.8606
Epoch 962/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3444 - acc: 0.8610
Epoch 963/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3403 - acc: 0.8619
Epoch 964/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3390 - acc: 0.8636
Epoch 965/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3378 - acc: 0.8626
Epoch 966/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3373 - acc: 0.8635
Epoch 967/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.3387 - acc: 0.8626
Epoch 968/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3414 - acc: 0.8583
Epoch

This procedure is the best to have a more robust accuracy results. In case the model that we are testing is computationally expensive, this procedure won't be applicable, for this reason another solution would be to set a random seed in order to have reproducible results.

In [65]:
mean_acc = accuracies.mean()
variance = accuracies.std()
mean_acc

0.8582500040531158

We will now tune the neural network using Grid Search. This technique will allow us to tune the hyperparameters of our model to improve the accuracy results.

In [66]:
classifier = KerasClassifier(build_fn = build_classifier, batch_size = 10000, epochs = 1000)
# Parameters that we want to optimize
parameters = { 'optimizer' : ['adam', 'rmsprop','nadam','adamax', 'sgd']}

In [67]:
# Grid Search with the parameter chosen
grid_search = GridSearchCV(estimator = classifier, param_grid = parameters, scoring = 'accuracy', cv = 10)
# Fit on training set
grid_search = grid_search.fit(X_train, y_train)

Epoch 1/1000
7200/7200 [==============================] - 10s 1ms/step - loss: 0.6932 - acc: 0.4635
Epoch 2/1000
7200/7200 [==============================] - 0s 2us/step - loss: 0.6926 - acc: 0.7285
Epoch 3/1000
7200/7200 [==============================] - 0s 5us/step - loss: 0.6919 - acc: 0.7965
Epoch 4/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.6912 - acc: 0.7971
Epoch 5/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.6903 - acc: 0.7971
Epoch 6/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.6895 - acc: 0.7971
Epoch 7/1000
7200/7200 [==============================] - 0s 5us/step - loss: 0.6886 - acc: 0.7971
Epoch 8/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.6877 - acc: 0.7971
Epoch 9/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.6867 - acc: 0.7971
Epoch 10/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.6856 - acc: 0.7971
Epoch 11

7200/7200 [==============================] - 0s 2us/step - loss: 0.4437 - acc: 0.7971
Epoch 84/1000
7200/7200 [==============================] - 0s 5us/step - loss: 0.4423 - acc: 0.7971
Epoch 85/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4401 - acc: 0.7971
Epoch 86/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4439 - acc: 0.7971
Epoch 87/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4423 - acc: 0.7971
Epoch 88/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4426 - acc: 0.7971
Epoch 89/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4411 - acc: 0.7971
Epoch 90/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4387 - acc: 0.7971
Epoch 91/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4407 - acc: 0.7971
Epoch 92/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4407 - acc: 0.7971
Epoch 93/1000


Epoch 165/1000
7200/7200 [==============================] - 0s 2us/step - loss: 0.4274 - acc: 0.7978
Epoch 166/1000
7200/7200 [==============================] - 0s 2us/step - loss: 0.4264 - acc: 0.7979
Epoch 167/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.4271 - acc: 0.7978
Epoch 168/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4254 - acc: 0.7983
Epoch 169/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.4254 - acc: 0.7992
Epoch 170/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4231 - acc: 0.7982
Epoch 171/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.4243 - acc: 0.7997
Epoch 172/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.4244 - acc: 0.8010
Epoch 173/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4253 - acc: 0.7996
Epoch 174/1000
7200/7200 [==============================] - 0s 6us/step - loss: 0.4246 - ac

Epoch 247/1000
7200/7200 [==============================] - 0s 2us/step - loss: 0.4143 - acc: 0.8279
Epoch 248/1000
7200/7200 [==============================] - 0s 5us/step - loss: 0.4152 - acc: 0.8292
Epoch 249/1000
7200/7200 [==============================] - 0s 2us/step - loss: 0.4118 - acc: 0.8293
Epoch 250/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.4147 - acc: 0.8274
Epoch 251/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.4119 - acc: 0.8304
Epoch 252/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.4131 - acc: 0.8321
Epoch 253/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4125 - acc: 0.8311
Epoch 254/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.4134 - acc: 0.8301
Epoch 255/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4138 - acc: 0.8288
Epoch 256/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4128 - ac

Epoch 329/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3973 - acc: 0.8388
Epoch 330/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.4027 - acc: 0.8342
Epoch 331/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3996 - acc: 0.8386
Epoch 332/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4008 - acc: 0.8390
Epoch 333/1000
7200/7200 [==============================] - 0s 3us/step - loss: 0.4005 - acc: 0.8371
Epoch 334/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.4003 - acc: 0.8390
Epoch 335/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3972 - acc: 0.8367
Epoch 336/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3987 - acc: 0.8390
Epoch 337/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3999 - acc: 0.8369
Epoch 338/1000
7200/7200 [==============================] - 0s 4us/step - loss: 0.3993 - ac

...

Epoch 670/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3520 - acc: 0.8555
Epoch 671/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3521 - acc: 0.8574
Epoch 672/1000
8000/8000 [==============================] - 0s 2us/step - loss: 0.3525 - acc: 0.8559
Epoch 673/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3515 - acc: 0.8570
Epoch 674/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3507 - acc: 0.8566
Epoch 675/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3514 - acc: 0.8569
Epoch 676/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3483 - acc: 0.8544
Epoch 677/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3530 - acc: 0.8529
Epoch 678/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3528 - acc: 0.8545
Epoch 679/1000
8000/8000 [==============================] - 0s 2us/step - loss: 0.3551 - ac

8000/8000 [==============================] - 0s 7us/step - loss: 0.3441 - acc: 0.8587
Epoch 752/1000
8000/8000 [==============================] - 0s 6us/step - loss: 0.3423 - acc: 0.8605
Epoch 753/1000
8000/8000 [==============================] - 0s 3us/step - loss: 0.3458 - acc: 0.8599
Epoch 754/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3455 - acc: 0.8600
Epoch 755/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3431 - acc: 0.8584
Epoch 756/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3440 - acc: 0.8577
Epoch 757/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3439 - acc: 0.8602
Epoch 758/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3404 - acc: 0.8605
Epoch 759/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3459 - acc: 0.8577
Epoch 760/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3440 - acc: 0.8570
Epoch

Epoch 833/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3388 - acc: 0.8596
Epoch 834/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3374 - acc: 0.8630
Epoch 835/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3367 - acc: 0.8602
Epoch 836/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3348 - acc: 0.8637
Epoch 837/1000
8000/8000 [==============================] - 0s 5us/step - loss: 0.3328 - acc: 0.8639
Epoch 838/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3378 - acc: 0.8609
Epoch 839/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3381 - acc: 0.8611
Epoch 840/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3369 - acc: 0.8637
Epoch 841/1000
8000/8000 [==============================] - 0s 2us/step - loss: 0.3379 - acc: 0.8630
Epoch 842/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3344 - ac

Epoch 915/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3303 - acc: 0.8636
Epoch 916/1000
8000/8000 [==============================] - 0s 2us/step - loss: 0.3301 - acc: 0.8648
Epoch 917/1000
8000/8000 [==============================] - 0s 2us/step - loss: 0.3327 - acc: 0.8661
Epoch 918/1000
8000/8000 [==============================] - 0s 5us/step - loss: 0.3363 - acc: 0.8658
Epoch 919/1000
8000/8000 [==============================] - 0s 3us/step - loss: 0.3339 - acc: 0.8608
Epoch 920/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3306 - acc: 0.8665
Epoch 921/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3318 - acc: 0.8649
Epoch 922/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3330 - acc: 0.8636
Epoch 923/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3326 - acc: 0.8629
Epoch 924/1000
8000/8000 [==============================] - 0s 2us/step - loss: 0.3326 - ac

Epoch 997/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3263 - acc: 0.8666
Epoch 998/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3332 - acc: 0.8635
Epoch 999/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3266 - acc: 0.8659
Epoch 1000/1000
8000/8000 [==============================] - 0s 4us/step - loss: 0.3291 - acc: 0.8659


In [68]:
best_parameter = grid_search.best_params_
best_accuracy = grid_search.best_score_
print('Best parameter: ' + str(best_parameter))
print('Best accuracy: ' + str(best_accuracy))

Best parameter: {'optimizer': 'rmsprop'}
Best accuracy: 0.86025
